# Capstone Project - The Battle of the Neighborhoods (Week 1)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a drugstore. Specifically, this report will be targeted to stakeholders interested in opening a **Japanese restaurant** in **Kuala Lumpur, Malaysia**.

Since there are lots of restaurants in Kuala Lumpur, we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Japanese restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promising neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decision are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Japanese restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centres of those areas will be obtained using **GeoPy reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* number of retail stores and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Kuala Lumpur centre will be obtained using **GeoPy geocoding** of well known Kuala Lumpur location (KLCC)


### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our are of interest which is approximately 12x12 kilometers centered around Kuala Lumpur city center.

Let's first find the latitude & longitude of Kuala Lumpur city center, using specific, well known addresses and GeoPy geocoding.

In [46]:
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

address = 'KLCC'

geolocator = Nominatim(user_agent="kl_explorer")
location = geolocator.geocode(address)
kl_latitude = location.latitude
kl_longitude = location.longitude
kl_center = [kl_latitude, kl_longitude]
print('Coordinate of {}: {}'.format(address, kl_center))

Coordinate of KLCC: [3.1593058, 101.7132025]


Now let's create a grid of area candidates, equally spaced, centered around city and within ~6km from KLCC. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhoods centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate systems (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in meters).

In [47]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def latlon_to_xy(lat, lon):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=48, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_latlon(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=48, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[1], lonlat[0]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Kuala Lumpur center latitude={}, longitude={}'.format(kl_center[0], kl_center[1]))
x, y = latlon_to_xy(kl_center[0], kl_center[1])
print('Kuala Lumpur center UTM X={}, Y={}'.format(x, y))
la, lo = xy_to_latlon(x, y)
print('Kuala Lumpur center latitude={}, longitude={}'.format(la, lo))

Coordinate transformation check
-------------------------------
Kuala Lumpur center latitude=3.1593058, longitude=101.7132025
Kuala Lumpur center UTM X=134613.2987436622, Y=349779.8427554232
Kuala Lumpur center latitude=3.1593057999999994, longitude=101.7132025


Let's create a **hexagonal grid of cells**: we offset every other way and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [48]:
kl_center_x, kl_center_y = latlon_to_xy(kl_center[0], kl_center[1]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = kl_center_x - 6000
x_step = 600
y_min = kl_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0 # 300 for alternate rows
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(kl_center_x, kl_center_y, x, y)
        if (distance_from_center <= 6001):
            lat, lon = xy_to_latlon(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')
#latitudes

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [49]:
#!pip install folium

import folium

In [146]:
map_kl = folium.Map(location=kl_center, zoom_start=13)
folium.Marker(kl_center, popup='KLCC').add_to(map_kl)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kl)
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_kl)
    #folium.Marker([lat, lon]).add_to(map_kl)
#folium.Circle([latitudes[0], longitudes[0]], radius=300, color='blue', fill=False).add_to(map_kl)
#folium.Circle([latitudes[25], longitudes[25]], radius=300, color='blue', fill=False).add_to(map_kl)
map_kl

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to its neighbors is exactly the same) and within ~6km from KLCC.

Let's now use GeoPy reverse geocoding to get approximate addresses of those locations.

In [51]:
def get_address(latitude, longitude):
    try:
        geolocator = Nominatim(user_agent="kl_explorer")
        latlon = str(latitude) + ", " + str(longitude)
        location = geolocator.reverse(latlon)
        return location
    except:
        return None

addr = get_address(kl_center[0], kl_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(kl_center[0], kl_center[1], addr))

Reverse geocoding check
-----------------------
Address of [3.1593058, 101.7132025] is: Avenue K, Jalan Ampang, Kampung Baru, Kuala Lumpur, 50400, Malaysia


In [52]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = str(address).replace(', Malaysia', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [53]:
addresses[150:170]

['Jalan Dagang 6/8, Taman Putra Sulaiman, Majlis Perbandaran Ampang Jaya, Selangor, 68000',
 'Jalan Dagang 1/4, Taman Dagang, Majlis Perbandaran Ampang Jaya, Selangor, 68000',
 'Jalan Pinang, Taman Kosas, Majlis Perbandaran Ampang Jaya, Selangor, 68000',
 'Lorong Dungun, Bukit Damansara, Kuala Lumpur, 50480',
 'Jalan Lembah Ledang, Kuala Lumpur, 50480',
 'Jalan Ledang, Taman Duta, Kuala Lumpur, 50480',
 'Lebuhraya Sultan Iskandar, Kuala Lumpur, 50580',
 'Jalan Berjasa, Chow Kit, Kuala Lumpur, 50580',
 'Asia School of Business, Jalan Sultan Salahuddin, Chow Kit, Kuala Lumpur, 50580',
 'Madras Store, Jalan Bunus 6, Chow Kit, Kuala Lumpur, 50100',
 'KL Forest Eco Park, Changkat Raja Chulan, Bukit Bintang, Kuala Lumpur, 50200',
 'Gravy Baby, Jalan Cangkat Perak, Bukit Bintang, Kuala Lumpur, 50250',
 'KLCC Convention Center, KLCC-Bukit Bintang Pedestrian Walkway, Bukit Bintang, Kuala Lumpur, 50088',
 'Naza Tower, 10, Persiaran KLCC, Bukit Bintang, Kuala Lumpur, 50088',
 'Jalan Taman U-Thant

Looking good. Let's now place all this into a Pandas dataframe.

In [54]:
import pandas as pd
df_locations = pd.DataFrame({
    'Address': addresses,
    'Latitude': latitudes,
    'Longitude': longitudes,
    'X': xs,
    'Y': ys,
    'Distance from center': distance_from_center
})

df_locations.head(10)

Address  Latitude   Longitude  \
0  Bandar Malaysia - High Speed Rail station to S...  3.107630  101.697191   
1                 Razak Mansion, Kuala Lumpur, 51020  3.107647  101.702582   
2                 Razak Mansion, Kuala Lumpur, 51020  3.107664  101.707973   
3  Bandar Sri Permaisuri, Cheras, Kuala Lumpur, 5...  3.107681  101.713364   
4  Jalan Siakep, Flat Sri Melaka (block 4E), Cher...  3.107697  101.718755   
5  Bandar Sri Permaisuri, Cheras, Kuala Lumpur, 5...  3.107714  101.724146   
6  Jalan Midah 1, Taman Midah, Cheras, Kuala Lump...  3.107731  101.729537   
7  Jalan Desa Seputeh 1, Seputeh Point, Seputeh, ...  3.112298  101.689090   
8                       Seputeh, Kuala Lumpur, 50460  3.112315  101.694481   
9  Jalan Lapangan Terbang Lama, Razak Mansion, Ta...  3.112332  101.699872   

               X              Y  Distance from center  
0  132813.298744  344064.075090            8286.73639  
1  133413.298744  344064.075090            8286.73639  
2  134013.298744  344064.075090            8286.73639  
3  134613.298744  344064.075090            8286.73639  
4  135213.298744  344064.075090            8286.73639  
5  135813.298744  344064.075090            8286.73639  
6  136413.298744  344064.075090            8286.73639  
7  131913.298744  344583.690333            8286.73639  
8  132513.298744  344583.690333            8286.73639  
9  133113.298744  344583.690333            8286.73639

... and let's now save/persist this data into local file.

In [55]:
df_locations.to_pickle('./locations.pkl')

### Foursquare API ###

Now that we have our location candidates, let's use Foursquare API to get into restaurants in each neighborhood.

We're interested in venues in 'Food' category. So we will include in out list only venues that have 'Food' in category name.

Foursquare credentials are defined below.

In [56]:
foursquare_client_id = 'VOIQ1IJZOVLYTNTKYMPWUYSCRUZPU5MR2QA2TJUXFR0MDX1Y' # your Foursquare ID
foursquare_client_secret = 'L5VJ03YG252BR5WOLJP1MQSSVSNG3XQ2HRFOMAVJ2TOPXWU1' # your Foursquare Secret

In [57]:
import requests

# Category IDs corresponding to Japanese restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

japanese_restaurant_categories = ['55a59bace4b013909087cb0c','55a59bace4b013909087cb30','55a59bace4b013909087cb21',
                                 '55a59bace4b013909087cb06','55a59bace4b013909087cb1b','55a59bace4b013909087cb1e',
                                 '55a59bace4b013909087cb18','55a59bace4b013909087cb24','55a59bace4b013909087cb15',
                                 '55a59bace4b013909087cb27','55a59bace4b013909087cb12','4bf58dd8d48988d1d2941735',
                                 '55a59bace4b013909087cb2d','55a59a31e4b013909087cb00','55a59af1e4b013909087cb03',
                                 '55a59bace4b013909087cb2a','55a59bace4b013909087cb0f','55a59bace4b013909087cb33',
                                 '55a59bace4b013909087cb09','55a59bace4b013909087cb36']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'ryori', 'shokuto']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Malaysia', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]
    except:
        venues = []
    return venues

In [76]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found Japanese restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    japanese_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, foursquare_client_id, foursquare_client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_japanese = is_restaurant(venue_categories, specific_filter=japanese_restaurant_categories)
            if is_res:
                x, y = latlon_to_xy(venue_latlon[0], venue_latlon[1])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_japanese, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_japanese:
                    japanese_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, japanese_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
japanese_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('japanese_restaurants_350.pkl', 'rb') as f:
        japanese_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, japanese_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('japanese_restaurants_350.pkl', 'wb') as f:
        pickle.dump(japanese_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)

Restaurant data loaded.


In [77]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Japanese restaurants:', len(japanese_restaurants))
print('Percentage of Japanese restaurants: {:.2f}%'.format(len(japanese_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())
len(restaurants)

Total number of restaurants: 3080
Total number of Japanese restaurants: 41
Percentage of Japanese restaurants: 1.33%
Average number of restaurants in neighborhood: 7.315934065934066


3080

In [83]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('524bb499498e8db87c662c58', '斋饭', 3.1072354316711426, 101.69904327392578, 'Malaysia', 210, False, 133019.33019345696, 344019.756126759)
('4e773dbb483b0cf5ed865bf3', '(King kong) ahmed maideen sg. Besi', 3.1091277365733867, 101.70274582567103, 'Flat razak mansion (Jln sungai besi), 57100 Kuala Lumpur, Kuala Lumpur', 165, False, 133432.06781630078, 344227.9783441066)
('4ced2a1b4cd4236a4c70a663', 'Roti Petak Razak Mension', 3.1090862687223955, 101.7026679912784, '57100 Kuala Lumpur, Federal Territory of Kuala Lum', 160, False, 133423.39076133748, 344223.4142278337)
('4ef00f270e01e1fde207f569', 'Sushi King Favorites', 3.10611840356321, 101.70024959451372, 'Sougate (Jalan Sg Besi), Kuala Lumpur, Kuala Lumpur', 310, False, 133153.20385912096, 343895.66242862976)
('4dff191ac65b10468961a767', 'Sg. Besi Corner Mamak Stall', 3.1090220452093544, 101.70634256216775, 'Jalan Besi Batu 3 1/2, 57100 Kuala Lumpur, Federal Territory of Kuala Lum', 236, Fa

In [84]:
print('List of Japanese restaurants')
print('---------------------------')
for r in list(japanese_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(japanese_restaurants))

List of Japanese restaurants
---------------------------
('5d1d51e3e7e5fc002381c8c5', 'IPPUDO Gardens Mall', 3.11984, 101.67845, 'Lot-T218 3rd Floor The Gardens Mall Lingkaran Syed Putra, The Gardens Mall, 59200 Kuala Lumpur, Kuala Lumpur', 202, True, 130731.73043860408, 345422.51535982767)
('4ff17e98e4b0e65c8e1687bb', 'Shushi-zen', 3.1187941455804844, 101.67854769602702, 'Malaysia', 319, True, 130742.23814014671, 345306.68457305647)
('58537573ce593d5304d38a7a', 'Sushi King', 3.1268973379715748, 101.72448199008879, 'Sunway Velocity (Lot 4-09, 4th Floor), 55100 Kuala Lumpur, Kuala Lumpur', 63, True, 135857.32828414644, 346187.79374844977)
('58523995040d5373852e2882', 'Sushi Zanmai (寿司三味)', 3.127788775997752, 101.72428812137153, 'Sunway Velocity', 146, True, 135836.0603522791, 346286.55611480115)
('5528b073498ea4c3e3843881', 'Sushi Mentai 壽司明太', 3.128689, 101.751241, '9-G, Jalan Perubatan 2, Pandan Indah, Pandan Indah, Kuala Lumpur', 236, True, 138835.9760795721, 346376.89217853476)
('59

In [85]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Ishq Restaurant, Museum Restaurant, Islamic Art Museum Malaysia
Restaurants around location 102: Kedai Makan City Parking, Heritage Station Restaurant, Rail Cafe, Kedai Mamak KTM, Ghandi Vegetarian Restaurant
Restaurants around location 103: Bawah Pokok Indian Rice, Restaurant Pik Wah (碧華樓酒家), 阿順哥鮑魚盤菜 Chef Soon Koh Restaurant Sdn Bhd, Ali, Muthu & Ah Hock, Wildflowers, Purple Cane 紫藤茶原, Back Alley Prawn Mee, 玉壶轩茶楼
Restaurants around location 104: Sarang Cookery, Warong Bomba Jln Hang Tuah, Vistana Corner, meeexx, 河清园源记茶餐室
Restaurants around location 105: Restoran Yap Hup Kee, Wong Mei Kee (王美记) Restaurant, Restoran Sin Hiap Kee, 福成水饺大王, 悦心軒素食館, Ayam Penyet Express, Purple Cane, The Zun Kitchenette 尊厨
Restaurants around location 106: Restaurant Onn Kee Claypot Seafood Porridge, 好想吃 Hxc Grand Ballroom, Restoran O.K. Kari Kepala Ikan (O.K.巴东咖哩鱼头餐厅海鲜粥家), Restoran New Ocean, Restoran Xin Dong Ting (新洞庭骨

Let's now see all the collected restaurants in our area of interest on map, and let's also show Japanese restaurants in different color.

In [86]:
map_kl = folium.Map(location=kl_center, zoom_start=13)
folium.Marker(kl_center, popup='KLCC').add_to(map_kl)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_japanese = res[6]
    color = 'red' if is_japanese else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_kl)
map_kl

Looking good. So now we have all the restaurants in area within few kilometers from KLCC, and we know which ones are Japanese restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Japanese restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Kuala Lumpur that have low restaurant density, particularly those with low number of Japanese restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Kuala Lumpur center (KLCC)**. We have also **identified Japanese restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of **'restaurant density'** across different areas of Kuala Lumpur - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Japanese restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Japanese restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [87]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 7.315934065934066


Address  Latitude   Longitude  \
0  Bandar Malaysia - High Speed Rail station to S...  3.107630  101.697191   
1                 Razak Mansion, Kuala Lumpur, 51020  3.107647  101.702582   
2                 Razak Mansion, Kuala Lumpur, 51020  3.107664  101.707973   
3  Bandar Sri Permaisuri, Cheras, Kuala Lumpur, 5...  3.107681  101.713364   
4  Jalan Siakep, Flat Sri Melaka (block 4E), Cher...  3.107697  101.718755   
5  Bandar Sri Permaisuri, Cheras, Kuala Lumpur, 5...  3.107714  101.724146   
6  Jalan Midah 1, Taman Midah, Cheras, Kuala Lump...  3.107731  101.729537   
7  Jalan Desa Seputeh 1, Seputeh Point, Seputeh, ...  3.112298  101.689090   
8                       Seputeh, Kuala Lumpur, 50460  3.112315  101.694481   
9  Jalan Lapangan Terbang Lama, Razak Mansion, Ta...  3.112332  101.699872   

               X              Y  Distance from center  Restaurants in area  \
0  132813.298744  344064.075090            8286.73639                    1   
1  133413.298744  344064.075090            8286.73639                    2   
2  134013.298744  344064.075090            8286.73639                    1   
3  134613.298744  344064.075090            8286.73639                    0   
4  135213.298744  344064.075090            8286.73639                    1   
5  135813.298744  344064.075090            8286.73639                    0   
6  136413.298744  344064.075090            8286.73639                    8   
7  131913.298744  344583.690333            8286.73639                    3   
8  132513.298744  344583.690333            8286.73639                    1   
9  133113.298744  344583.690333            8286.73639                    3   

   Distance to Japanese restaurant  
0                            10000  
1                            10000  
2                            10000  
3                            10000  
4                            10000  
5                            10000  
6                            10000  
7                            10000  
8                            10000  
9                            10000

OK, now let's calculate the **distance to nearest Japanese restaurant from every area condidate center** (not only those within 300m - we want dsitance to closest one, regardless of how distant it is).

In [88]:
distances_to_japanese_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in japanese_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_japanese_restaurant.append(min_distance)

df_locations['Distance to Japanese restaurant'] = distances_to_japanese_restaurant

In [89]:
df_locations.head(10)

Address  Latitude   Longitude  \
0  Bandar Malaysia - High Speed Rail station to S...  3.107630  101.697191   
1                 Razak Mansion, Kuala Lumpur, 51020  3.107647  101.702582   
2                 Razak Mansion, Kuala Lumpur, 51020  3.107664  101.707973   
3  Bandar Sri Permaisuri, Cheras, Kuala Lumpur, 5...  3.107681  101.713364   
4  Jalan Siakep, Flat Sri Melaka (block 4E), Cher...  3.107697  101.718755   
5  Bandar Sri Permaisuri, Cheras, Kuala Lumpur, 5...  3.107714  101.724146   
6  Jalan Midah 1, Taman Midah, Cheras, Kuala Lump...  3.107731  101.729537   
7  Jalan Desa Seputeh 1, Seputeh Point, Seputeh, ...  3.112298  101.689090   
8                       Seputeh, Kuala Lumpur, 50460  3.112315  101.694481   
9  Jalan Lapangan Terbang Lama, Razak Mansion, Ta...  3.112332  101.699872   

               X              Y  Distance from center  Restaurants in area  \
0  132813.298744  344064.075090            8286.73639                    1   
1  133413.298744  344064.075090            8286.73639                    2   
2  134013.298744  344064.075090            8286.73639                    1   
3  134613.298744  344064.075090            8286.73639                    0   
4  135213.298744  344064.075090            8286.73639                    1   
5  135813.298744  344064.075090            8286.73639                    0   
6  136413.298744  344064.075090            8286.73639                    8   
7  131913.298744  344583.690333            8286.73639                    3   
8  132513.298744  344583.690333            8286.73639                    1   
9  133113.298744  344583.690333            8286.73639                    3   

   Distance to Japanese restaurant  
0                      2415.237121  
1                      2945.953678  
2                      2812.583489  
3                      2461.257897  
4                      2219.223961  
5                      2124.175025  
6                      2195.286790  
7                      1376.264367  
8                      1912.949642  
9                      2478.840265

In [90]:
print('Average distance to closest Japanese restaurant from each area center:', df_locations['Distance to Japanese restaurant'].mean())

Average distance to closest Japanese restaurant from each area center: 1153.0770302980463


OK, so **on average Japanese restaurant can be found approximately 1km** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's create a map showing **heatmap/density of restaurants** and try to extract soem meaningful info from that. Also, let's show a few circles indication distance of 1km, 2km and 3km from KLCC.

In [91]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

japanese_latlons = [[res[2], res[3]] for res in japanese_restaurants.values()]

In [92]:
from folium import plugins
from folium.plugins import HeatMap

map_kl = folium.Map(location=kl_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_kl) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_kl)
folium.Marker(kl_center).add_to(map_kl)
folium.Circle(kl_center, radius=1000, fill=False, color='white').add_to(map_kl)
folium.Circle(kl_center, radius=2000, fill=False, color='white').add_to(map_kl)
folium.Circle(kl_center, radius=3000, fill=False, color='white').add_to(map_kl)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_kl

Looks like a few pockets of low restaurant density closest to city centre can be found **north and west from KLCC**.

Let's create another heatmap showing **heatmap/density of Japanese restaurants** only.

In [93]:
map_kl = folium.Map(location=kl_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_kl)
#cartodbpositron cartodbdark_matter
HeatMap(japanese_latlons).add_to(map_kl)
folium.Marker(kl_center).add_to(map_kl)
folium.Circle(kl_center, radius=1000, fill=False, color='white').add_to(map_kl)
folium.Circle(kl_center, radius=2000, fill=False, color='white').add_to(map_kl)
folium.Circle(kl_center, radius=3000, fill=False, color='white').add_to(map_kl)
map_kl

This map is not 'hot' (Japanese restaurants represent a subset of ~1.33% of all restaurants in Kuala Lumpur) but it also indicates higher density of existing Japanese restaurants directly south from KLCC, with closest pockets of **low Japanese restaurant density positioned east, north and west from city center**.

Based on this we will now focus our analysis on areas *south-east and east from KCLL* - we will move the center of our area of interest and reduce its size to have a radius of **2.5km**. This places our location candidates mostly at **Bukit Bintang**. 

### Bukit Bintang

The area has long been Kuala Lumpur's most prominent retail belt that is home to many landmark shopping centres, al-fresco cafés, bars, night markets, food street as well as hawker-type eateries. This area is popular among tourists and locals, especially among the youths.

Nestled within Kuala Lumpur's Golden Triangle, the Bukit Bintang district begins with Bukit Bintang Road which starts at Raja Chulan Road and ends at Pudu Road. The two other roads that border the Bukit Bintang district are Sultan Ismail Road which intersects it and Imbi Road at the south. Walter Grenier Road, Bulan Road, Changkat Bukit Bintang and Alor Road are considered part of the entertainment district.

Bukit Bintang borders Pudu and Cheras to the south, Petaling Street to the west, Bukit Nanas to the north, KLCC to the northeast and Tun Razak Exchange and Maluri to the east.

Let's define new, more narrow region of interest, which will include low-restaurant-count parts of Bukit Bintang closest to KLCC.

In [147]:
roi_x_min = kl_center_x - 700
roi_y_max = kl_center_y + 800
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lat, roi_center_lon = xy_to_latlon(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_kl = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_kl)
folium.Marker(kl_center).add_to(map_kl)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_kl)
map_kl

Not bad - this nicely covers all the pockets of low restaurant density in Bukit Bintang closest to KLCC.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m apart).

In [109]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lat, lon = xy_to_latlon(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Japanese restaurants**.

In [111]:
def count_restaurants_nearby(x, y, restaurants, radius=250):
    count = 0
    for res in restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_japanese_distance = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, japanese_restaurants)
    roi_japanese_distance.append(distance)
print('done.')

Generating data on location candidates... done.


In [112]:
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Japanese restaurant':roi_japanese_distance})

df_roi_locations.head(10)

Latitude   Longitude              X              Y  Restaurants nearby  \
0  3.121420  101.729045  136363.298744  345579.842755                  24   
1  3.121423  101.729944  136463.298744  345579.842755                  24   
2  3.122187  101.724101  135813.298744  345666.445296                   8   
3  3.122190  101.725000  135913.298744  345666.445296                   6   
4  3.122193  101.725898  136013.298744  345666.445296                   2   
5  3.122196  101.726797  136113.298744  345666.445296                   4   
6  3.122198  101.727695  136213.298744  345666.445296                  12   
7  3.122201  101.728594  136313.298744  345666.445296                  23   
8  3.122204  101.729492  136413.298744  345666.445296                  21   
9  3.122207  101.730391  136513.298744  345666.445296                  18   

   Distance to Japanese restaurant  
0                       790.955445  
1                       858.373233  
2                       523.204367  
3                       524.344258  
4                       544.179192  
5                       580.796940  
6                       631.283753  
7                       692.613362  
8                       762.172789  
9                       837.914944

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Japanese restaurants in radius of 400 meters**.

In [113]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_jap_distance = np.array(df_roi_locations['Distance to Japanese restaurant']>=400)
print('Locations with no Japanese restaurants within 400m:', good_jap_distance.sum())

good_locations = np.logical_and(good_res_count, good_jap_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 698
Locations with no Japanese restaurants within 400m: 1768
Locations with both conditions met: 639


Let's see how this looks on a map.

In [114]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_kl = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_kl)
HeatMap(restaurant_latlons).add_to(map_kl)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_kl)
folium.Marker(kl_center).add_to(map_kl)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kl) 
map_kl

Looking good. We now have a bunch of locations fairly close to KLCC (mostly in Bukit Bintang), and we know that each of those locations has no more than two restaurants in radius of 250m, and no Japanese restaurant closer than 400m. Any of those locations is a potential candidate for a new Japanese restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [115]:
map_kl = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_kl)
folium.Marker(kl_center).add_to(map_kl)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kl)
map_kl

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Japanese restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [117]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_latlon(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_kl = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_kl)
HeatMap(restaurant_latlons).add_to(map_kl)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_kl)
folium.Marker(kl_center).add_to(map_kl)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_kl) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kl)
map_kl

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [141]:
map_kl = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(kl_center).add_to(map_kl)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_kl)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kl)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_kl)
map_kl

Let's zoom in on candidate areas in **Bukit Bintang**:

In [142]:
map_kl = folium.Map(location=[3.1524, 101.7298], zoom_start=15)
folium.Marker(kl_center).add_to(map_kl)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_kl) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_kl)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_kl)
map_kl

Finally, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [144]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lat, lon in cluster_centers:
    addr = str(get_address(lat, lon)).replace(', Malaysia', '')
    candidate_area_addresses.append(addr)    
    x, y = latlon_to_xy(lat, lon)
    d = calc_xy_distance(x, y, kl_center_x, kl_center_y)
    print('{}{} => {:.1f}km from KLCC'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

Jalan Penggawa, Taman U-Thant, Kuala Lumpur, 50538 => 2.2km from KLCC
Majlis Perbandaran Ampang Jaya, Selangor, 50988    => 3.6km from KLCC
Royal Selangor Golf Club, Jalan Belangkas 2, Taman Maluri, Kampung Pandan, Kuala Lumpur, 50600 => 2.0km from KLCC
Jalan Sultan Ismail, Maluri, Pudu, Kuala Lumpur, 55100 => 2.2km from KLCC
Jalan Ampang, Taman U-Thant, Kuala Lumpur, 50538   => 1.3km from KLCC
8, Jalan Pandan Kemajuan A, Taman Ampang Hilir, Kampung Pandan Dalam, Majlis Perbandaran Ampang Jaya, Selangor, 50600 => 4.0km from KLCC
Terowong Smart, Maluri, Cheras, Kuala Lumpur, 55100 => 3.5km from KLCC
Jalan Langgak Golf, Taman U-Thant, Kuala Lumpur, 55000 => 1.7km from KLCC
Persiaran KLCC, Bukit Bintang, Kuala Lumpur, 50450 => 0.9km from KLCC
Jalan Lingkaran Tengah 2, Taman Bakti, Pandan Indah, Majlis Perbandaran Ampang Jaya, Selangor, 51500 => 4.5km from KLCC
Jalan 1/91, Pudu Ulu, Cheras, Kuala Lumpur, 51500  => 4.3km from K

In [145]:
map_kl = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(kl_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_kl)
for latlon, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([latlon[0], latlon[1]], popup=addr).add_to(map_kl) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_kl)
map_kl

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Kuala Lumpur (~3000 in our initial are of interest which was 12x12km around KLCC), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected south and west from KLCC, so we focused our attention to areas south-east, corresponding to Bukit Bintang district. It offers a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-east from KLCC) we first created a dense grid of location candidates (spaced 100m apart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Japanese restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Japanese restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Kuala Lumpur center but not crowded with existing restaurants (particularly Japanese) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the are. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

Our analysis shows that although there is a great number of restaurants in Berlin (~2000 in our initial area of interest which was 12x12km around Alexanderplatz), there are pockets of low restaurant density fairly close to city center. Highest concentration of restaurants was detected north and west from Alexanderplatz, so we focused our attention to areas south, south-east and east, corresponding to boroughs Kreuzberg, Friedrichshain and south-east corner of central Mitte borough. Another borough was identified as potentially interesting (Prenzlauer Berg, north-east from Alexanderplatz), but our attention was focused on Kreuzberg and Friedrichshain which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.
## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Kuala Lumpur areas close to center with low number of restaurants (particularly Japanese restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Japanese restaurant. By calculating restaurant density distribution from Foursquare data we have first identified a general district that justify further analysis (Bukit Bintang), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decision on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.